In [1]:
%reload_ext autoreload
%autoreload 2

## Imports

In [1]:
import os,sys
module_path = os.path.abspath(os.path.join('C://Users//Rodrigo//Desktop//PhD//Study1//Physiological_Data//'))
if module_path not in sys.path:
    sys.path.append(module_path)

In [2]:
from Load import *
from Process_Features import *
import numpy as np
import biosignalsnotebooks as bsnb
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")

## Load Files

In [3]:
path = "C://Users//Rodrigo//Desktop//PhD//loop-system//Breathing Rate//Data_Analysis//"

participants_data={}

for user in os.listdir(path):
    participant_path = os.path.join(path,user)
    
    if os.path.isdir(participant_path):
        participants_data[user] = {}
        for file in os.listdir(participant_path):
            if file.endswith('.xdf'):
                file_path = os.path.join(participant_path,file)
                
                condition = file.split("_")[1].split(".")[0]
                
                data = Run_files(file_path)
                
                participants_data[user][condition] = data

Stream 3: Calculated effective sampling rate 0.6189 Hz is different from specified rate 50.0000 Hz.
Stream 2: Calculated effective sampling rate 0.7198 Hz is different from specified rate 50.0000 Hz.
Stream 2: Calculated effective sampling rate 66.2452 Hz is different from specified rate 50.0000 Hz.
Stream 3: Calculated effective sampling rate 0.8801 Hz is different from specified rate 50.0000 Hz.
Stream 3: Calculated effective sampling rate 0.6201 Hz is different from specified rate 50.0000 Hz.
Stream 2: Calculated effective sampling rate 74.5119 Hz is different from specified rate 50.0000 Hz.
Stream 4: Calculated effective sampling rate 74.5324 Hz is different from specified rate 50.0000 Hz.
Stream 2: Calculated effective sampling rate 0.8285 Hz is different from specified rate 50.0000 Hz.
Stream 2: Calculated effective sampling rate 74.5283 Hz is different from specified rate 50.0000 Hz.
Stream 3: Calculated effective sampling rate 0.6351 Hz is different from specified rate 50.0000 

## Function to Load Breathing Rate

In [4]:
def Load_BreathingRate(data, stream_type: str):

    BR_Data = {}
    
    for stream in data:
        if stream["info"]["type"][0] == stream_type:
            BR_Data["Time"] = stream["time_stamps"]
            for i in range(0, int(stream["info"]["channel_count"][0])):
                BR_Data["BR"] = stream["time_series"][:, i]

    return BR_Data

## Function to rename dict key

In [5]:
def change_key(dictionary, key_to_remove, new_key):
    dictionary[new_key] = dictionary.pop(key_to_remove)

## Load Signals by condition

In [6]:
participants_signals={}
for user in participants_data:
    start_time = 0
    participants_signals[user] = {}
    for condition in participants_data[user]:
        participants_signals[user][condition] = {}
        match(condition):
            case "Baseline":
                
                baseline_data, baseline_fs = Load_Opensignals(participants_data[user][condition],"OpenSignals")
                change_key(baseline_data,"time_Opensignals","Time"),change_key(baseline_data,"CH1","ECG"),
                change_key(baseline_data,"CH2","EDA"),change_key(baseline_data,"CH3","RESP")
                start_time = baseline_data["Time"][0]
                baseline_data["Time"] = (baseline_data["Time"] - start_time) #/ 60
                
                baseline_markers, baseline_timestamps = Load_PsychopyMarkers(participants_data[user][condition],"PsychoPy Markers")
                baseline_timestamps = (baseline_timestamps - start_time) #/ 60
                
                baseline_BR = Load_BreathingRate(participants_data[user][condition],"Breathing Rate")
                baseline_BR["Time"] = (baseline_BR["Time"] - start_time) #/ 60

                participants_signals[user][condition]= {"Signals": baseline_data,
                                                        "BreathingRate": baseline_BR,
                                                        "Markers": baseline_markers, 
                                                        "Markers Timestamps": baseline_timestamps}
           
            case "PreStroop":
                
                PreStroop_Data, fs = Load_Opensignals(participants_data[user][condition],"OpenSignals")
                change_key(PreStroop_Data,"time_Opensignals","Time"),change_key(PreStroop_Data,"CH1","ECG"),
                change_key(PreStroop_Data,"CH2","EDA"),change_key(PreStroop_Data,"CH3","RESP")
                PreStroop_Data["Time"] = (PreStroop_Data["Time"] - start_time) #/ 60
                
                PreStroop_markers, PreStroop_timestamps = Load_PsychopyMarkers(participants_data[user][condition],"PsychoPy Markers")
                PreStroop_timestamps = (PreStroop_timestamps - start_time)# / 60
                
                PreStroop_BR = Load_BreathingRate(participants_data[user][condition],"Breathing Rate")
                PreStroop_BR["Time"] = (PreStroop_BR["Time"] - start_time) #/ 60

                participants_signals[user][condition]= {"Signals": PreStroop_Data,
                                                        "BreathingRate": PreStroop_BR,
                                                        "Markers": PreStroop_markers, 
                                                        "Markers Timestamps": PreStroop_timestamps}
                
            case "VR":
                
                VR_Data, fs = Load_Opensignals(participants_data[user][condition],"OpenSignals")
                change_key(VR_Data,"time_Opensignals","Time"),change_key(VR_Data,"CH1","ECG"),
                change_key(VR_Data,"CH2","EDA"),change_key(VR_Data,"CH3","RESP")
                
                VR_markers, VR_timestamps = Load_PsychopyMarkers(participants_data[user][condition],"PsychoPy Markers")
                
                if user == "P1":
                    VR_markers.append(['end','0'])
                    VR_timestamps.append(VR_Data["Time"][-1])
                
                VR_Data["Time"] = (VR_Data["Time"] - start_time) #/ 60
                VR_timestamps = (VR_timestamps - start_time) #/ 60
                
                VR_BR = Load_BreathingRate(participants_data[user][condition],"Breathing Rate")
                VR_BR["Time"] = (VR_BR["Time"] - start_time) #/ 60
                
                valence, arousal, valence_timestamps, arousal_timestamps = Load_Ratings(participants_data[user][condition],"PsychoPy Ratings")
                valence_timestamps = (valence_timestamps - start_time) #/ 60
                arousal_timestamps = (arousal_timestamps - start_time) #/ 60
                
                
                participants_signals[user][condition]= {"Signals": VR_Data,
                                                        "BreathingRate": VR_BR,
                                                        "Markers": VR_markers, 
                                                        "Markers Timestamps": VR_timestamps,
                                                        "Valence":valence,
                                                        "Valence Timestamps": valence_timestamps,
                                                        "Arousal": arousal,
                                                        "Arousal Timestamps": arousal_timestamps,
                                                        }
            case "PostStroop":
                
                PostStroop_Data, fs = Load_Opensignals(participants_data[user][condition],"OpenSignals")
                change_key(PostStroop_Data,"time_Opensignals","Time"),change_key(PostStroop_Data,"CH1","ECG"),
                change_key(PostStroop_Data,"CH2","EDA"),change_key(PostStroop_Data,"CH3","RESP")
                PostStroop_Data["Time"] = (PostStroop_Data["Time"] - start_time) #/ 60 
                
                PostStroop_markers, PostStroop_timestamps = Load_PsychopyMarkers(participants_data[user][condition],"PsychoPy Markers")
                PostStroop_timestamps = (PostStroop_timestamps - start_time) #/ 60
                
                PostStroop_BR = Load_BreathingRate(participants_data[user][condition],"Breathing Rate")
                PostStroop_BR["Time"] = (PostStroop_BR["Time"] - start_time) #/ 60

                participants_signals[user][condition]= {"Signals": PostStroop_Data,
                                                        "BreathingRate": PostStroop_BR,
                                                        "Markers": PostStroop_markers, 
                                                        "Markers Timestamps": PostStroop_timestamps}

In [7]:
participants_signals

{'P1': {'Baseline': {'Signals': {'Time': array([0.00000000e+00, 9.99787997e-03, 1.99957599e-02, ...,
           3.09344404e+02, 3.09354402e+02, 3.09364400e+02]),
    'ECG': array([-0.05678, -0.05193, -0.05067, ...,  0.21311,  0.42263,  0.28032],
          dtype=float32),
    'EDA': array([2.9339, 2.9312, 2.9312, ..., 3.8147, 3.8193, 3.867 ], dtype=float32),
    'RESP': array([ 0.44421,  0.48047,  0.50308, ..., -0.30826, -0.30515, -0.30029],
          dtype=float32)},
   'BreathingRate': {'Time': array([5.62706665e-03, 4.56252263e-01, 8.04343160e-01, ...,
           3.08180058e+02, 3.08527659e+02, 3.08740154e+02]),
    'BR': array([15.169001, 16.01367 , 16.01248 , ...,  9.084261, 10.239564,
           10.283673], dtype=float32)},
   'Markers': [['baseline', '0'], ['baseline', '1']],
   'Markers Timestamps': array([  6.38997601, 306.39418763])},
  'PostStroop': {'Signals': {'Time': array([2659.11796204, 2659.12796107, 2659.1379601 , ..., 2948.33976852,
           2948.34976755, 2948.3597

## Get Markers for Epochs

In [8]:
def getMarkers(marker, timestamps):
    videos, onset, offset = list(), list(), list()
    
    for timestamp, markers in zip(timestamps, marker):
        if markers[1] == '1':
            offset.append(timestamp)
        elif markers[0] == "end":
            offset.append(timestamp)
        else:
            onset.append(timestamp)
            videos.append(markers[0])

    return onset, offset, videos

In [9]:
participants_markers={}
for user in participants_signals:
    participants_markers[user] = {}
    for condition in participants_signals[user]:
        onset, offset, marker = getMarkers(participants_signals[user][condition]["Markers"],participants_signals[user][condition]["Markers Timestamps"])
        onset_index, offset_index = getMarkersIndex(onset,offset,participants_signals[user][condition]["Signals"]["Time"])
        events_diff = CalculateEventsDiff(onset,offset)
        participants_markers[user][condition] = {"Onset": onset, "Onset_index": onset_index, 
                                                 "Offset": offset, "Offset_index": offset_index,
                                                 "EventsDiff": events_diff,
                                                 "Marker": marker}

In [10]:
participants_markers

{'P1': {'Baseline': {'Onset': [6.389976005128119],
   'Onset_index': [640],
   'Offset': [306.3941876346362],
   'Offset_index': [30645],
   'EventsDiff': [300.00421162950806],
   'Marker': ['baseline']},
  'PostStroop': {'Onset': [2697.3163026560214,
    2699.8197491793544,
    2702.030872274714,
    2703.979273320234,
    2706.2749498936464,
    2707.3512368181837,
    2708.1692811493413,
    2708.8303923796047,
    2709.590400570829,
    2711.2967306294595,
    2713.735100322927,
    2714.9451911533833,
    2715.8933909445186,
    2716.4979228531593,
    2717.476960337546,
    2718.4103961405926,
    2719.027410008537,
    2719.8856186518096,
    2720.768958215893,
    2721.83867605665,
    2722.743877299421,
    2723.668559390644,
    2724.834932664002,
    2725.673763860308,
    2726.3003451501136,
    2728.0854968135827,
    2729.315592199622,
    2732.463787144108,
    2733.40785228234,
    2734.90606668737,
    2735.7456326932297,
    2736.4339977708296,
    2737.1970929017407,

In [11]:
br_markers={}
for user in participants_signals:
    br_markers[user] = {}
    for condition in participants_signals[user]:
        br_onset_index = np.where(participants_signals[user][condition]["BreathingRate"]["Time"] >= participants_markers[user][condition]["Onset"][0])[0][0]
        br_offset_index = np.where(participants_signals[user][condition]["BreathingRate"]["Time"] <= participants_markers[user][condition]["Offset"][-1])[0][-1]
        
        br_markers[user][condition] = {"Onset_index": [br_onset_index], "Offset_index": [br_offset_index]}

In [12]:
br_markers

{'P1': {'Baseline': {'Onset_index': [20], 'Offset_index': [1032]},
  'PostStroop': {'Onset_index': [30], 'Offset_index': [892]},
  'PreStroop': {'Onset_index': [0], 'Offset_index': [798]},
  'VR': {'Onset_index': [0], 'Offset_index': [2838]}},
 'P10': {'Baseline': {'Onset_index': [8], 'Offset_index': [1024]},
  'PostStroop': {'Onset_index': [29], 'Offset_index': [741]},
  'PreStroop': {'Onset_index': [138], 'Offset_index': [1068]},
  'VR': {'Onset_index': [10], 'Offset_index': [3159]}},
 'P11': {'Baseline': {'Onset_index': [9], 'Offset_index': [1015]},
  'PostStroop': {'Onset_index': [22], 'Offset_index': [557]},
  'PreStroop': {'Onset_index': [38], 'Offset_index': [701]},
  'VR': {'Onset_index': [22], 'Offset_index': [2929]}},
 'P12': {'Baseline': {'Onset_index': [7], 'Offset_index': [1038]},
  'PostStroop': {'Onset_index': [41], 'Offset_index': [709]},
  'PreStroop': {'Onset_index': [154], 'Offset_index': [907]},
  'VR': {'Onset_index': [50], 'Offset_index': [3025]}},
 'P13': {'Basel

## Create Epochs

In [13]:
from Signals_Processing import *

In [14]:
participants_epochs={}
for user in participants_signals:
    participants_epochs[user] = {}
    for condition in participants_signals[user]:
        signals = nk.epochs_create(pd.DataFrame.from_dict(participants_signals[user][condition]["Signals"]),
                                                        events = [participants_markers[user][condition]["Onset_index"][0]],
                                                        sampling_rate = 100,
                                                        epochs_start = 0,
                                                        epochs_end = (participants_markers[user][condition]["Offset_index"][-1] 
                                                                      - participants_markers[user][condition]["Onset_index"][0])/100,
                                                        )
        br = nk.epochs_create(pd.DataFrame.from_dict(participants_signals[user][condition]["BreathingRate"]),
                                                        events = br_markers[user][condition]["Onset_index"],
                                                        sampling_rate = len(participants_signals[user][condition]["BreathingRate"]["Time"])/
                                                                            (participants_signals[user][condition]["BreathingRate"]["Time"][-1]-
                                                                             participants_signals[user][condition]["BreathingRate"]["Time"][0]),
                                                        epochs_start = 0,
                                                        epochs_end = participants_signals[user][condition]["BreathingRate"]["Time"][br_markers[user][condition]["Offset_index"][0]] 
                                                                      - participants_signals[user][condition]["BreathingRate"]["Time"][br_markers[user][condition]["Onset_index"][0]] ,
                                                        )
        
        participants_epochs[user][condition] = {"Signals": signals, "BR": br}

In [15]:
participants_epochs

{'P1': {'Baseline': {'Signals': {'1':                   Time      ECG     EDA     RESP  Index Label
    0.000000      6.398643  0.03127  3.3134 -0.80154    640     1
    0.010000      6.408641 -0.10099  3.2791 -0.80173    641     1
    0.020001      6.418639 -0.08068  3.2600 -0.79985    642     1
    0.030001      6.428637 -0.06523  3.3081 -0.79541    643     1
    0.040001      6.438635 -0.06469  3.3092 -0.79523    644     1
    ...                ...      ...     ...      ...    ...   ...
    300.009999  306.335042 -0.00539  3.4412  0.34726  30640     1
    300.019999  306.345040 -0.00647  3.4443  0.33609  30641     1
    300.029999  306.355038 -0.00557  3.4412  0.33765  30642     1
    300.040000  306.365036 -0.00359  3.4882  0.32080  30643     1
    300.050000  306.375034 -0.00341  3.4546  0.32501  30644     1
    
    [30005 rows x 6 columns]},
   'BR': {'1':                   Time         BR  Index Label
    0.000000      6.517773  13.568778     20     1
    0.297062      6.65681

## Extract Features

In [ ]:
features_epochs={}
AVG_BR = []
for user in participants_epochs:
    features_epochs[user] = {}
    for condition in participants_epochs[user]:
        for epoch in participants_epochs[user][condition]["Signals"]:
            features_epochs[user][condition] = getDataframe(participants_epochs[user][condition]["Signals"][epoch],100,16)
            AVG_BR.append(np.mean(participants_epochs[user][condition]["BR"][epoch]["BR"]))

In [ ]:
features_epochs

## Full Dataframe

In [ ]:
dataframe = pd.DataFrame(columns=features_epochs["P1"]["Baseline"].columns)
users, conditions = [],[]
for user in features_epochs:
    for condition in features_epochs[user]:
        users.append(user)
        conditions.append(condition)
        dataframe = pd.concat([dataframe, features_epochs[user][condition]],ignore_index=True)
dataframe["Avg BR"] = AVG_BR
dataframe["User"] = users
dataframe["Condition"] = conditions
dataframe = dataframe.rename(columns={"AVG": "AVG_RSP_Rate", "Maximum": "Max_RSP_Rate", "Minimum": "Min_RSP_Rate", "STD": "STD_RSP_Rate"})

In [ ]:
dataframe

In [ ]:
dataframe.to_csv(r'C:\Users\Rodrigo\Desktop\PhD\loop-system\Breathing Rate\Results\dataframe.csv')

## Visualize Signals

 ECG+EDA+RESP

In [40]:
%matplotlib qt
colors = ["yellow", "blue","green","red"]
for participant in participants_epochs:
    if participant == "P1":
        plt.figure()
        plt.title(participant)
        hasLegend = True
        for i,condition in enumerate(participants_epochs[participant]):
            plt.text((participants_signals[participant][condition]["Markers Timestamps"][0] + participants_signals[participant][condition]["Markers Timestamps"][-1]) / 2, 6, condition, color='black', fontsize=12, ha='center', va='center', bbox=dict(facecolor='white', alpha=0.5))
            plt.axvspan(participants_signals[participant][condition]["Markers Timestamps"][0],participants_signals[participant][condition]["Markers Timestamps"][-1],color=colors[i],alpha=0.2)
            plt.plot(participants_epochs[participant][condition]["Signals"]["1"]["Time"],participants_epochs[participant][condition]["Signals"]["1"]["ECG"],
                     c='r',label="ECG" if hasLegend else "")
            plt.plot(participants_epochs[participant][condition]["Signals"]["1"]["Time"],participants_epochs[participant][condition]["Signals"]["1"]["EDA"],
                     c='b',label="EDA" if hasLegend else "")
            plt.plot(participants_epochs[participant][condition]["Signals"]["1"]["Time"],participants_epochs[participant][condition]["Signals"]["1"]["RESP"],
                     c='k',label="RESP" if hasLegend else "")
            hasLegend = False
        plt.legend()

In [ ]:
participants_signals["P1"]

In [104]:
from brokenaxes import brokenaxes

%matplotlib 
colors = ["yellow", "blue","green","red"]
conditions = ["Baseline", "Pre-Stroop", "VR", "Post-Stroop"]
for participant in participants_epochs:
    print(conditions)
    if participant == "P1":
        # Extract all timestamps and find discontinuity
        all_timestamps = []
        for condition in participants_signals[participant]:
            all_timestamps.append(participants_signals[participant][condition]["Markers Timestamps"][0])
            all_timestamps.append(participants_signals[participant][condition]["Markers Timestamps"][-1])
        all_timestamps = sorted(all_timestamps)
    
        # Determine discontinuities
        discontinuities = []
        for i in range(0, len(all_timestamps), 2):
            discontinuity_start = all_timestamps[i]
            discontinuity_end = all_timestamps[i + 1]
            discontinuities.append((discontinuity_start/60, discontinuity_end/60))
        
        sorted_discontinuities = (discontinuities[0], discontinuities[3],discontinuities[1],discontinuities[2])
        
        fig = plt.figure()
        bax = brokenaxes(xlims=discontinuities, wspace=0.1)
        for i, condition in enumerate(participants_epochs[participant]):
    
            times = participants_epochs[participant][condition]["Signals"]["1"]["Time"]/60
            ecg = participants_epochs[participant][condition]["Signals"]["1"]["ECG"]
            eda = participants_epochs[participant][condition]["Signals"]["1"]["EDA"]
            resp = participants_epochs[participant][condition]["Signals"]["1"]["RESP"]
            
            # Plot signals
            bax.plot(times, ecg, c='r', label="ECG" if hasLegend else "")
            bax.plot(times, eda, c='b', label="EDA" if hasLegend else "")
            bax.plot(times, resp, c='k', label="RESP" if hasLegend else "")
    
            # Paint background for each condition
            start_time = participants_signals[participant][condition]["Markers Timestamps"][0]/60
            end_time = participants_signals[participant][condition]["Markers Timestamps"][-1]/60
            bax.axvspan(start_time, end_time, facecolor=colors[i % len(colors)], alpha=0.3)

        for index, ax in enumerate(bax.axs):
            ticks = [round(discontinuities[index][0],1), round(discontinuities[index][1],1)]
            ax.set_xticks(ticks)
            ax.set_title(conditions[index],fontsize=24)
            ax.tick_params(axis='both', which='major', rotation=90, labelsize=32)
            
        # Add labels and a legend
        bax.set_xlabel('Time (min)',labelpad = 50, fontsize=44)
        bax.set_ylabel('Amplitude',labelpad = 50, fontsize=44)
        bax.legend()

        plt.show()

Using matplotlib backend: qtagg
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseline', 'Pre-Stroop', 'VR', 'Post-Stroop']
['Baseli

ECG

In [ ]:
%matplotlib notebook
colors = ["yellow", "blue","green","red"]
for participant in participants_signals:
    plt.figure()
    plt.title(participant)
    hasLegend = True
    for i,condition in enumerate(participants_signals[participant]):
        plt.text((participants_signals[participant][condition]["Markers Timestamps"][0] + participants_signals[participant][condition]["Markers Timestamps"][-1]) / 2, 6, condition, color='black', fontsize=12, ha='center', va='center', bbox=dict(facecolor='white', alpha=0.5))
        plt.axvspan(participants_signals[participant][condition]["Markers Timestamps"][0],participants_signals[participant][condition]["Markers Timestamps"][-1],color=colors[i],alpha=0.2)
        plt.plot(participants_signals[participant][condition]["Signals"]["Time"],participants_signals[participant][condition]["Signals"]["ECG"],
                 c='k',label="ECG" if hasLegend else "")
        hasLegend = False
    plt.legend()

EDA

In [ ]:
%matplotlib notebook
colors = ["yellow", "blue","green","red"]
for participant in participants_signals:
    plt.figure()
    plt.title(participant)
    hasLegend = True
    for i,condition in enumerate(participants_signals[participant]):
        plt.text((participants_signals[participant][condition]["Markers Timestamps"][0] + participants_signals[participant][condition]["Markers Timestamps"][-1]) / 2, 6, condition, color='black', fontsize=12, ha='center', va='center', bbox=dict(facecolor='white', alpha=0.5))
        plt.axvspan(participants_signals[participant][condition]["Markers Timestamps"][0],participants_signals[participant][condition]["Markers Timestamps"][-1],color=colors[i],alpha=0.2)
        plt.plot(participants_signals[participant][condition]["Signals"]["Time"],participants_signals[participant][condition]["Signals"]["EDA"],
                 c='k',label="EDA" if hasLegend else "")
    plt.legend()

RESP

In [ ]:
%matplotlib notebook
colors = ["yellow", "blue","green","red"]
for participant in participants_signals:
    plt.figure()
    plt.title(participant)
    hasLegend = True
    for i,condition in enumerate(participants_signals[participant]):
        plt.text((participants_signals[participant][condition]["Markers Timestamps"][0] + participants_signals[participant][condition]["Markers Timestamps"][-1]) / 2, 6, condition, color='black', fontsize=12, ha='center', va='center', bbox=dict(facecolor='white', alpha=0.5))
        plt.axvspan(participants_signals[participant][condition]["Markers Timestamps"][0],participants_signals[participant][condition]["Markers Timestamps"][-1],color=colors[i],alpha=0.2)
        plt.plot(participants_signals[participant][condition]["Signals"]["Time"],participants_signals[participant][condition]["Signals"]["RESP"],
                 c='k',label="RESP" if hasLegend else "")
        hasLegend = False
    plt.legend()

Breathing Rate

In [ ]:
%matplotlib notebook
colors = ["yellow", "blue","green","red"]
for participant in participants_signals:
    plt.figure()
    plt.title(participant)
    hasLegend = True
    for i,condition in enumerate(participants_signals[participant]):
        plt.text((participants_signals[participant][condition]["Markers Timestamps"][0] + participants_signals[participant][condition]["Markers Timestamps"][-1]) / 2, 6, condition, color='black', fontsize=12, ha='center', va='center', bbox=dict(facecolor='white', alpha=0.5))
        plt.axvspan(participants_signals[participant][condition]["Markers Timestamps"][0],participants_signals[participant][condition]["Markers Timestamps"][-1],color=colors[i],alpha=0.2)
        plt.plot(participants_signals[participant][condition]["BreathingRate"]["Time"],participants_signals[participant][condition]["BreathingRate"]["BR"],
                 c='k',label="BR" if hasLegend else "")
        hasLegend = False
    plt.legend()